# Churn Prediction Inference - Batch or serverless real-time


After running AutoML we saved our best model our MLflow registry.

All we need to do now is use this model to run Inferences. A simple solution is to share the model name to our Data Engineering team and they'll be able to call this model within the pipeline they maintained.

This can be done as part of a DLT pipeline or a Workflow in a separate job.
Here is an example to show you how MLflow can be directly used to retrieve the model and run inferences.

##Deploying the model for batch inferences

<img style="float: right; margin-left: 20px" width="600" src="https://github.com/QuentinAmbard/databricks-demo/raw/main/retail/resources/images/churn_batch_inference.gif" />

Now that our model is available in the Registry, we can load it to compute our inferences and save them in a table to start building dashboards.

We will use MLFlow function to load a pyspark UDF and distribute our inference in the entire cluster. If the data is small, we can also load the model with plain python and use a pandas Dataframe.

If you don't know how to start, Databricks can generate a batch inference notebook in just one click from the model registry: Open MLFlow model registry and click the "User model for inference" button!

## 5/ Enriching the gold data with a ML model
<div style="float:right">
  <img width="500px" src="https://github.com/QuentinAmbard/databricks-demo/raw/main/retail/resources/images/lakehouse-retail/lakehouse-retail-churn-de-small-4.png"/>
</div>

Our Data scientist team has built a churn prediction model using Auto ML and saved it into Databricks Model registry. 

A key value of the Lakehouse is that we can easily load this model and predict our churn right into our pipeline. 

Note that we don't have to worry about the model framework (sklearn or other), MLflow abstracts all that for us.

In [0]:
%run ./includes/SetupLab

In [0]:
spark.sql("use catalog main")
spark.sql("use database "+databaseForDLT)
print("Database name: " + databaseForDLT)
print("User name: " + userName)

Database name: odl_user_1513183_databrickslabs_com_retail_dlt
User name: odl_user_1513183_databrickslabs_com


In [0]:
import mlflow
#                                      Stage/version
#                       Model name          |              output
#                           |               |                 |
mlflow.set_registry_uri('databricks-uc')
modelURL = "models:/" + 'main.'+databaseForDLT+'.'+modelName + "@production"    #        |
print("Retrieving model " + modelURL)                #        |
predict_churn_udf = mlflow.pyfunc.spark_udf(spark, modelURL, "int")
#We can use the function in SQL
spark.udf.register("predict_churn", predict_churn_udf)

Retrieving model models:/main.odl_user_1513183_databrickslabs_com_retail_dlt.retail_churn_odl_user_1513183_databrickslabs_com@production


2024/11/16 00:19:06 WARNING mlflow.pyfunc: Calling `spark_udf()` with `env_manager="local"` does not recreate the same environment that was used during training, which may lead to errors or inaccurate predictions. We recommend specifying `env_manager="conda"`, which automatically recreates the environment that was used to train the model and performs inference in the recreated environment.


2024/11/16 00:19:06 INFO mlflow.models.flavor_backend_registry: Selected backend for flavor 'python_function'


In [0]:
model_features = predict_churn_udf.metadata.get_input_schema().input_names()
predictions = spark.table('churn_features').withColumn('churn_prediction', predict_churn_udf(*model_features))
predictions.createOrReplaceTempView("v_churn_prediction")

In [0]:
%sql
create or replace table churn_prediction as select * from v_churn_prediction

num_affected_rows num_inserted_rows

In [0]:
%sql
select * from churn_prediction

user_id email creation_date last_activity_date firstname lastname address channel country gender age_group churn order_count total_amount total_item last_transaction platform event_count session_count last_event days_since_creation days_since_last_activity days_last_event churn_prediction 95d6ac28-e966-4a53-a86e-650a3cf1af26 51969eb4e1347f3f8deaa2bb60f4b079e95ca177 2023-05-10T00:00:00Z 2024-11-08T07:40:07Z Troy Snyder 395 Mark Parks Apt. 739
North Coreyville, HI 09312 WEBAPP SPAIN 1 4 1 3 172 6 2024-11-15T06:55:03Z ios 3 3 2024-11-01T14:20:14Z 555 7 14 1 eabaac61-6b6c-4fdc-bc20-35be93e5c5b2 7aabd0c304e43f54b3499149273fd0ec76450d9f 2023-09-17T00:00:00Z 2024-11-13T03:30:06Z Lori Hoover 704 Frank Ports
East Angel, VT 09339 PHONE SPAIN 1 8 0 3 217 7 2024-11-15T15:58:25Z ios 3 3 2024-11-04T07:01:57Z 425 2 11 0 20bcfb39-c4c1-4d78-b3bf-a4cb8144c053 e9d84cdd44d1737f78fca68470240cedd96e3537 2023-12-28T00:00:00Z 2024-11-04T06:19:30Z Jeffrey Robinson 789 Horton Spur Suite 583
Jaimebury, ND 31929 WEBAPP USA 1 6 1 4 166 8 2024-11-11T22:39:58Z ios 4 4 2024-11-09T05:02:23Z 323 11 6 1 5301ebca-c701-4f0a-93f2-db3edec7192a 6d154edf80c87ae5a3d3788432957a4c0b504b61 2023-08-30T00:00:00Z 2024-11-04T03:38:35Z Jason Lewis 045 Michael Trail Apt. 368
Port Andrewshire, ND 49952 WEBAPP FR 1 9 0 2 55 3 2024-11-02T17:39:41Z ios 2 2 2024-11-08T12:27:52Z 443 11 7 0 6eae2648-cc47-4783-9277-ef6126ee5278 54407f1c8d204ff853f5532a9b5f19d72759c8d7 2023-10-31T00:00:00Z 2024-11-05T11:18:45Z Kevin Turner 21823 Nicholas Estate Apt. 661
Smithtown, GU 60195 WEBAPP SPAIN 1 5 1 4 127 6 2024-11-14T09:12:25Z other 4 4 2024-11-12T23:19:49Z 381 10 3 1 a62dbf3d-5cc0-4f71-a48d-7f65d71fa8ee 9f6bb5562ee779270a4c4522363f704f1f9f25e6 2023-11-05T00:00:00Z 2024-11-07T15:11:08Z Shane West 322 Diane Parks
Yoderfurt, LA 38703 WEBAPP USA 0 2 1 1 40 2 2024-11-06T05:24:45Z other 1 1 2024-11-15T12:57:03Z 376 8 0 1 f9e4f615-4252-4a9f-a0ca-e42435e22dce 88ad23d4ab213b9eea96611a99f01bc42bffc9f1 2023-10-06T00:00:00Z 2024-11-07T22:13:10Z Taylor Mcdonald USNV Curry
FPO AP 71072 WEBAPP FR 0 2 1 4 187 9 2024-11-13T08:55:46Z android 4 4 2024-11-10T13:27:31Z 406 8 5 1 afd40761-6f62-4a82-add7-fd198e4b4c5d fcf149ed7c9a1ff2645ff3141d939ea3c47f6a5a 2024-05-27T00:00:00Z 2024-11-04T23:07:24Z Joseph Adams 660 Mark Isle
East Jon, PA 40213 WEBAPP USA 1 8 1 3 168 8 2024-11-09T23:44:06Z ios 3 3 2024-11-02T01:45:13Z 172 11 13 1 122cf027-a28f-4641-8b34-a97e750b0f05 0c4fa8863ab6230b020c862044bebc14fb07de9c 2024-04-07T00:00:00Z 2024-11-09T12:09:53Z Autumn Andrews 3540 Samuel Ports Suite 945
North Gregoryport, CO 47634 MOBILE FR 1 7 1 5 191 9 2024-11-09T17:56:41Z other 5 5 2024-11-15T00:20:04Z 222 6 0 1 3466fc6c-0d35-448f-a48e-767f6ba2f1be e29839a8f5c9b5ccb327947025269574863090f2 2024-10-10T00:00:00Z 2024-11-12T16:14:38Z Kristina Kramer 48716 Kaitlyn Park Apt. 425
Samanthaside, MA 10297 PHONE USA 1 0 1 2 125 5 2024-11-07T22:53:17Z other 2 2 2024-11-13T10:04:44Z 36 3 2 1 4330043a-a5b8-4f19-8838-3953561626c3 ea474ec80d64fda1ff5459ff15c218dafd97f2c5 2024-09-10T00:00:00Z 2024-11-12T20:52:50Z Laurie Solis 2056 Gabriel Trace Suite 360
Lake Jonathanmouth, AS 98889 PHONE SPAIN 0 6 1 1 38 1 2024-11-11T17:38:17Z other 1 1 2024-11-11T10:24:57Z 66 3 4 1 aae79825-ce0a-432e-8353-70506d783c7b 898f005255f6dcd016aab01dfcaaa78f54d0a636 2024-09-14T00:00:00Z 2024-11-14T16:12:08Z Sandra Mclean 60735 John Extensions Suite 432
Jenniferfort, MA 83432 PHONE FR 1 6 1 4 196 8 2024-11-14T17:14:10Z other 4 3 2024-11-15T04:40:07Z 62 1 0 1 97650950-f58a-41cb-9bf1-8da505f14fc7 7ac42821916afbdcf207de16f3e62aeeef414482 2024-08-23T00:00:00Z 2024-11-03T19:14:07Z Jaime Lopez 012 Jeffrey Bridge
New Lisa, GA 12904 WEBAPP USA 1 9 1 1 87 3 2024-11-10T18:58:14Z other 1 1 2024-11-13T06:39:02Z 84 12 2 1 97cb584f-1b20-4b5d-9d0d-9a47060c2a80 e57ce61ed16a5847619d5dc0582f816b32544b49 2024-10-03T00:00:00Z 2024-11-09T11:40:02Z Ashley Berry 11065 Stephens Cliffs
East Angela, AZ 54368 MOBILE FR 0 5 1 3 182 6 2024-11-15T14:39:06Z ios 3 3 2024-11-05T05:04:32Z 43 6 10 1 